In [10]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

# Imports
import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

# Our application logic will be added here
def cnn_model_fn(features, labels, mode):
    """Model function for CNN."""
    # Input Layer
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

    # Convolutional Layer #1
    conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

    # Pooling Layer #1
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

    # Convolutional Layer #2 and Pooling Layer #2
    conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

    # Dense Layer
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
    dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

    # Logits Layer
    logits = tf.layers.dense(inputs=dropout, units=10)

    predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }

    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for both TRAIN and EVAL modes)
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

    # Configure the Training Op (for TRAIN mode)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(loss=loss, global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {"accuracy": tf.metrics.accuracy(labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

def main(unused_argv):
    # Load training and eval data
    mnist = tf.contrib.learn.datasets.load_dataset("mnist")
    train_data = mnist.train.images # Returns np.array
    train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
    eval_data = mnist.test.images # Returns np.array
    eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)
    
    # Create the Estimator
    mnist_classifier = tf.estimator.Estimator(
    model_fn=cnn_model_fn, model_dir=r"C:\astrodata\CNN\model\mnist_convnet_model")
    
    # Set up logging for predictions
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=50)
    
    # Train the model
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": train_data},
        y=train_labels,
        batch_size=100,
        num_epochs=None,
        shuffle=True)
    mnist_classifier.train(
        input_fn=train_input_fn,
        steps=20000,
        hooks=[logging_hook])
    
    # Evaluate the model and print results
    eval_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": eval_data},
        y=eval_labels,
        num_epochs=1,
        shuffle=False)
    eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
    print(eval_results)

if __name__ == "__main__":
    tf.app.run()

Extracting MNIST-data\train-images-idx3-ubyte.gz
Extracting MNIST-data\train-labels-idx1-ubyte.gz
Extracting MNIST-data\t10k-images-idx3-ubyte.gz
Extracting MNIST-data\t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': 'C:\\astrodata\\CNN\\model\\mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x0000027BB55E0828>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evalua

INFO:tensorflow:loss = 2.3006365, step = 0
INFO:tensorflow:probabilities = [[0.07359908 0.09568601 0.0914501  0.09057456 0.11031412 0.10249344
  0.12386293 0.09622552 0.11574075 0.10005345]
 [0.08381376 0.0978144  0.08624385 0.09246583 0.10719902 0.11383392
  0.11097841 0.10122529 0.10662593 0.09979957]
 [0.08682517 0.08950205 0.09876681 0.0989778  0.10077406 0.09758099
  0.11869451 0.09913104 0.10181763 0.1079299 ]
 [0.08667081 0.11520059 0.08478829 0.09181188 0.10697598 0.11153074
  0.12135836 0.09253508 0.09879088 0.09033743]
 [0.08782253 0.10349521 0.08145665 0.09033161 0.1072701  0.10164787
  0.11998437 0.09235555 0.10689218 0.10874394]
 [0.09656258 0.09190129 0.09671928 0.09280583 0.10844511 0.09971513
  0.11224672 0.08890827 0.10347482 0.109221  ]
 [0.08976634 0.10842413 0.09775025 0.10494451 0.09297502 0.10583538
  0.11073317 0.09134869 0.10637159 0.09185094]
 [0.09419743 0.10034451 0.08870617 0.08823984 0.09370079 0.10052587
  0.11415423 0.09171687 0.11250256 0.11591178]
 [0.0

INFO:tensorflow:global_step/sec: 77.5796
INFO:tensorflow:probabilities = [[0.1102258  0.10399853 0.0764797  0.09708755 0.1065442  0.09515887
  0.10911715 0.08603551 0.10937312 0.10597959]
 [0.08607098 0.10347887 0.08590898 0.10382006 0.10520386 0.09738693
  0.10514005 0.09329329 0.11196864 0.10772828]
 [0.08595514 0.08770058 0.08596293 0.09856554 0.11749244 0.08652781
  0.11076872 0.09341205 0.11128258 0.12233222]
 [0.08795352 0.10149473 0.09085588 0.09196518 0.10571685 0.10343076
  0.1127727  0.1085349  0.10711827 0.09015721]
 [0.08852641 0.10155338 0.09058347 0.09234772 0.09762117 0.10089433
  0.11450559 0.09668352 0.10716766 0.11011678]
 [0.09969929 0.09850688 0.08675277 0.09290707 0.09720661 0.10947669
  0.10615896 0.08982058 0.11957936 0.0998918 ]
 [0.10664427 0.08616209 0.09632406 0.09904221 0.10554635 0.11709492
  0.11154921 0.08348197 0.10166671 0.09248825]
 [0.09638985 0.08843541 0.10212513 0.09610294 0.10968962 0.08438072
  0.12995045 0.08820335 0.0979181  0.10680448]
 [0.100

INFO:tensorflow:loss = 2.268628, step = 100 (1.294 sec)
INFO:tensorflow:probabilities = [[0.09360755 0.10657129 0.08212019 0.10458708 0.09945461 0.10095902
  0.12025949 0.09505311 0.09434386 0.10304384]
 [0.09512489 0.0900625  0.08893133 0.10916508 0.09684917 0.10329317
  0.10086489 0.10079695 0.11037023 0.10454179]
 [0.09776761 0.09659187 0.0946532  0.09679725 0.0993866  0.09890114
  0.1066633  0.09213909 0.11746681 0.09963311]
 [0.111869   0.10177874 0.07703494 0.09456889 0.11308821 0.09469409
  0.11255716 0.08810794 0.11003876 0.09626226]
 [0.08232522 0.10433384 0.08406445 0.09562194 0.09685329 0.10344154
  0.10881909 0.09982346 0.11244405 0.11227313]
 [0.10465765 0.08730435 0.08174951 0.09305588 0.10260648 0.10331272
  0.11367258 0.10052755 0.11007064 0.1030426 ]
 [0.09014683 0.08372781 0.09119251 0.11881258 0.12154786 0.10233273
  0.10925131 0.08559412 0.0898128  0.10758143]
 [0.09761498 0.11389239 0.09100994 0.08950683 0.10048654 0.10354451
  0.10078617 0.09168541 0.11913319 0.09

INFO:tensorflow:global_step/sec: 90.8682
INFO:tensorflow:probabilities = [[0.08757336 0.09475618 0.08670239 0.09580433 0.10676337 0.12212103
  0.0955461  0.08754441 0.10645261 0.11673616]
 [0.08910447 0.09753957 0.09329101 0.1005829  0.09714851 0.09514169
  0.1091722  0.11212816 0.10814495 0.0977466 ]
 [0.09539393 0.10527439 0.08851419 0.09638485 0.09496431 0.10179916
  0.12138425 0.08944296 0.10627652 0.10056545]
 [0.10252988 0.09149193 0.09366246 0.09851306 0.09319798 0.11492573
  0.10706513 0.08308017 0.11228237 0.10325135]
 [0.09108343 0.0863322  0.10974263 0.09574705 0.09254359 0.10556593
  0.1045455  0.09947072 0.10692792 0.10804103]
 [0.10596305 0.09406175 0.10135372 0.09390686 0.10469153 0.09208001
  0.11001976 0.0888543  0.10181125 0.10725776]
 [0.09432867 0.1071352  0.09220868 0.09329012 0.09654307 0.10805331
  0.10915101 0.08400255 0.11268862 0.10259871]
 [0.10501841 0.09601294 0.08916134 0.10604455 0.10204066 0.1067216
  0.10058943 0.09352819 0.1096098  0.09127299]
 [0.0856

...

INFO:tensorflow:loss = 0.081121884, step = 19800 (1.066 sec)
INFO:tensorflow:probabilities = [[0.00000006 0.00000924 0.00013543 0.9992138  0.         0.00063781
  0.00000001 0.         0.00000351 0.00000003]
 [0.00000048 0.00000023 0.00552036 0.9925041  0.         0.00079646
  0.00000002 0.00000206 0.00117418 0.00000212]
 [0.0000187  0.99405366 0.00027981 0.00210925 0.00048272 0.00027654
  0.00051077 0.00031396 0.00174142 0.00021313]
 [0.         0.00000009 0.00007403 0.99931633 0.         0.0002681
  0.         0.00000001 0.00026674 0.00007472]
 [0.0000002  0.00000001 0.00000257 0.00004827 0.00022499 0.00000086
  0.00000001 0.00286658 0.0000283  0.99682826]
 [0.00000073 0.00000002 0.00001286 0.00004104 0.00000178 0.00006386
  0.00000008 0.00000024 0.99985445 0.00002492]
 [0.00084104 0.00009838 0.99461836 0.00415724 0.00000025 0.00000154
  0.00000411 0.00014189 0.00013692 0.00000022]
 [0.00022197 0.00006623 0.00128845 0.00000485 0.00322832 0.00012656
  0.9946779  0.00000252 0.00036316 

INFO:tensorflow:global_step/sec: 93.7568
INFO:tensorflow:probabilities = [[0.9938543  0.00001488 0.00082741 0.00066102 0.00004059 0.00246632
  0.00072365 0.00009864 0.00018518 0.00112806]
 [0.00000532 0.00000048 0.00000532 0.0002175  0.00281191 0.00044948
  0.00000113 0.00958254 0.00040373 0.9865226 ]
 [0.00003005 0.00004149 0.00234834 0.00092171 0.00000069 0.00027364
  0.00000024 0.00504747 0.99110305 0.00023339]
 [0.00077338 0.00001927 0.0001381  0.00049024 0.01681065 0.04408149
  0.00134571 0.00947347 0.0055389  0.92132884]
 [0.0005998  0.00162505 0.00200946 0.97270477 0.00000625 0.01761801
  0.00003699 0.00007874 0.00456474 0.00075612]
 [0.09984832 0.00598691 0.02179634 0.03599462 0.06769607 0.0157387
  0.73910064 0.00297018 0.00829801 0.00257013]
 [0.00026208 0.99519485 0.00014189 0.00004282 0.00006975 0.00004443
  0.00141357 0.00001133 0.00279216 0.00002708]
 [0.00051074 0.00022338 0.00050107 0.00411587 0.00078756 0.00138895
  0.00000224 0.4126754  0.00495308 0.5748417 ]
 [0.0777

INFO:tensorflow:loss = 0.11141723, step = 19900 (1.068 sec)
INFO:tensorflow:probabilities = [[0.00000143 0.00009745 0.00002587 0.00383376 0.00160437 0.00020066
  0.00000015 0.05180962 0.0011246  0.94130206]
 [0.0000578  0.9973322  0.00084637 0.00001156 0.00033867 0.00001682
  0.00090832 0.00007046 0.00040689 0.00001088]
 [0.00234646 0.95360905 0.00093745 0.00058181 0.00164033 0.00028325
  0.00914265 0.00070444 0.03058499 0.00016961]
 [0.00000683 0.00000083 0.00002603 0.00002194 0.00000082 0.000014
  0.00000101 0.00000017 0.99992645 0.00000187]
 [0.00000122 0.00000426 0.00002716 0.996736   0.0000004  0.00165621
  0.00000001 0.00001364 0.00018308 0.00137802]
 [0.00000002 0.00000026 0.00202408 0.9977977  0.00000001 0.0000743
  0.         0.00000002 0.00010312 0.00000053]
 [0.00001131 0.9959485  0.00001489 0.00013067 0.00016036 0.00003121
  0.00042911 0.0000133  0.00316654 0.00009419]
 [0.0000011  0.00006171 0.00004613 0.000535   0.9531454  0.00011349
  0.00000319 0.00259103 0.00015402 0.0

INFO:tensorflow:Saving checkpoints for 20000 into C:\astrodata\CNN\model\mnist_convnet_model\model.ckpt.
INFO:tensorflow:Loss for final step: 0.13243343.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-12-28-10:04:31
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from C:\astrodata\CNN\model\mnist_convnet_model\model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-12-28-10:04:32
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9684, global_step = 20000, loss = 0.099802375
INFO:tensorflow:Saving 'checkpoint_path' summary for global step 20000: C:\astrodata\CNN\model\mnist_convnet_model\model.ckpt-20000
{'accuracy': 0.9684, 'loss': 0.099802375, 'global_step': 20000}


SystemExit: 